In [1]:
# 필요한 모듈과 라이브러리를 로딩
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.common.by import By
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.keys import Keys
import pandas as pd
import time, os, math, random, sys, datetime
from datetime import date, timedelta, datetime
import pyautogui
from tqdm import tqdm
import re

# chromedriver 자동 설치
import chromedriver_autoinstaller

from selenium.webdriver.common.action_chains import ActionChains


In [2]:
# 작업 시간과 고유 dir 등 생성
n = time.localtime()
s = '%04d-%02d-%02d' % (n.tm_year, n.tm_mon, n.tm_mday)
s_time = time.time( )


a = datetime.now()-timedelta(days=6)
a = a.strftime('%Y-%m-%d')
b = datetime.now()-timedelta(days=7)
b = b.strftime('%Y-%m-%d')
print(a, b)

2021-05-01 2021-04-30


In [3]:
print("=" *80)
print("         SLRCLUB 크롤러입니다.")
print("=" *80)

f_dir = os.path.expanduser('~') + f'\\Desktop\\crawler-bot\\COMMUNITY\\{b}-{a}\\' # 운영체제 상관없이 바탕화면 'crawler-bot' 폴더에 작업

print("=" *80)
print("데이터 크롤링을 시작합니다.")
print("=" *80)

         SLRCLUB 크롤러입니다.
데이터 크롤링을 시작합니다.


In [4]:
# 저장될 파일 경로와 이름을 지정
# 파일을 저장할 폴더 위치를 만들고, 중복일 경우 해당 폴더를 삭제하고 새로 생성합니다.
try : 
    os.makedirs(f_dir)
except : pass
else : 
    os.chdir(f_dir)

fc_name=f_dir+'\\'+f'slr3.csv'

In [5]:
# 크롤링 데이터가 들어갈 리스트 생성
domain2 = []    # 크롤링 도메인
keyword2 = []   # 크롤링 키워드
title2 = []     # 게시물 제목
user2 = []      # 게시물 작성자
url2 = []       # 게시물 url
time2 = []      # 게시물 작성 시간
view_cnt2 = []  # 게시물 뷰 카운트
like_cnt2 = []  # 추천/공감 카운트
text2 = []      # 게시물 내용
com_cnt2 = []   # 댓글 수
com_user2 = []  # 댓글 user
com_text2 = []  # 댓글 user_id & text

In [6]:
# chromedriver-autoinstaller 이용
chromedriver_autoinstaller.install(cwd=True)

# HEADLESS MODE
options = webdriver.ChromeOptions()
# options.add_argument('headless')
options.add_argument('window-size=1920x1080') 
# options.add_argument("--disable-gpu")
options.add_experimental_option('excludeSwitches', ['enable-logging'])
options.add_argument("user-agent=Mozilla/5.0 (Macintosh; Intel Mac OS X 10_12_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/61.0.3163.100 Safari/537.36")
args = ["hide_console", ]

# 알림창 끄기
options.add_experimental_option("prefs", {"profile.default_content_setting_values.notifications": 1})

# 웹사이트 접속 후 해당 메뉴로 이동
driver = webdriver.Chrome(options=options,service_args=args)
driver.maximize_window()

In [7]:
# 1. SLR CLUB 자유게시판 크롤링
query_url= ('http://www.slrclub.com/bbs/zboard.php?id=free')
driver.get(query_url)
driver.implicitly_wait(5)
time.sleep(1)
driver.find_element_by_link_text("2").click()
time.sleep(1)
driver.find_element_by_link_text("1").click()
time.sleep(1)

cur_url = driver.current_url        
page_num = int(cur_url.split("&page=")[1]) - 250
print("현재 페이지 :", page_num)

현재 페이지 : 729971


In [8]:
domain1 = "SLR CLUB"
print("==========",domain1,"크롤링 진행 중 ==========")

========== SLR CLUB 크롤링 진행 중 ==========


In [9]:
html = driver.page_source
soup = BeautifulSoup(html, 'html.parser')
item_box = soup.find('tbody').find_all(name='tr')
item_box

[<tr>
 <td class="list_notice">공지</td>
 <td class="sbj"><a href="/bbs/vx2.php?id=help&amp;page=730221&amp;no=32">SLRCLUB 게시판 관리규정 : 자유게시판 관리규정 및 자주 묻는 질문</a></td>
 <td class="list_name"><div class="bh slr_admin"></div></td>
 <td class="list_date no_att"><span title="2013년 10월 24일 16시 42분 41초">2013/10/24</span></td>
 <td class="list_vote no_att">0</td>
 <td class="list_click no_att">342215</td>
 </tr>,
 <tr>
 <td class="list_num no_att">38636198</td>
 <td class="sbj"><a href="/bbs/vx2.php?id=free&amp;page=730221&amp;no=38636198">인도는 서양 vs  동양</a> [2]</td>
 <td class="list_name"><span class="lop" data-track="38636198" data-xuid="1776731">임마후닥</span></td>
 <td class="list_date no_att">14:04:32</td>
 <td class="list_vote no_att">0</td>
 <td class="list_click no_att">65</td>
 </tr>,
 <tr>
 <td class="list_num no_att">38636197</td>
 <td class="sbj"><a href="/bbs/vx2.php?id=free&amp;page=730221&amp;no=38636197">남자들이 원하는 그것</a> [4]</td>
 <td class="list_name"><span class="lop" data-track="3863

In [10]:
# driver.get('http://www.slrclub.com/bbs/zboard.php?id=free&page=730094&prev_no=38058147')

# print(len(item_box))

# html = driver.page_source
# soup = BeautifulSoup(html, 'html.parser')
# item_box = soup.find('tbody').find_all(name='tr')
# item_box

# for item in item_box :
#     if item.td['class'] == ['list_notice'] :
#         print("notice!")
#     else :
#         print(item.td['class'])

In [11]:
# page_num = 15   # 현재 페이지 넘버
while_code = 0

while True :
    
    if while_code == 1:
        break

    target_page = f"http://www.slrclub.com/bbs/zboard.php?id=free&page={page_num}"
    driver.get(target_page)
    time.sleep(1)

    html = driver.page_source
    soup = BeautifulSoup(html, 'html.parser')
    soup = soup.find(name='div', attrs={'id':'slrct'})
    item_box = soup.find(name='tbody').find_all(name='tr')

    for i in item_box :
        if i.td['class'] != ['list_notice'] and len(i.find(name='td', attrs={'class':'list_date no_att'}).text.strip().replace("/","-")) > 1:
            to_day = a
            target_day = b
            
            to_day = to_day[2:]
            target_day = target_day[2:]
            
            # 게시글에 날짜가 지정되어 있으면 가져오고 에러로 가져오지 못하면 전 게시물 날짜 사용
            try :
                i.find(name='td', attrs={'class':'list_date no_att'}).text.strip().replace("/","-")
                post_day = i.find(name='td', attrs={'class':'list_date no_att'}).text.strip().replace("/","-")
            except :
                pass
            
            
            print(post_day > to_day, to_day != datetime.now().strftime('%Y-%m-%d'), ":" in post_day, post_day >= target_day)
            print(post_day, to_day, target_day)
            
            if  post_day > to_day or ( to_day != datetime.now().strftime('%Y-%m-%d') and ":" in post_day) :
#                 print(post_day, to_day)
                pass           
            
            elif post_day >= target_day :
                try :
                    print('href :',i.find(name='td', attrs={'class':'sbj'}).find('a')['href'] )


                    target_url = "http://www.slrclub.com"+i.find(name='td', attrs={'class':'sbj'}).find('a')['href']
                    print("target_url :", target_url)
                    driver.get(target_url)
                    time.sleep(1)
                    print("domain :", domain1)
    #                 print("keyword :", keyword)

                    post_html = driver.page_source
                    post_soup = BeautifulSoup(post_html, 'html.parser')
                    post_box = post_soup.find(name='div', attrs={'id':'slrct'})
                
#                     print(post_box)

                    # title
                    title1 = post_box.find(name='td', attrs={'class':'sbj'}).text.strip().split("\n")   
                    print("title :", title1)

                    # user_id
                    user1 = post_box.find(name='td', attrs={'class':'nick'}).text        
                    print("user_id :", user1)
                    
                        
                    # time
                    time1 = post_box.find(name='td', attrs={'class':'date bbs_ct_small'}).text.replace("/","-").strip()
                    print("작성 시간 :", time1)

                    # view
                    view_cnt1 = post_box.find(name='td', attrs={'class':'click bbs_ct_small'}).text
                    print("조회수 :", view_cnt1)

                    # like
                    try :
                        like_cnt1 = post_box.find(name='td', attrs={'class':'vote bbs_ct_small'}).text
                    except :
                        like_cnt1 = 0
                    print("공감/좋아요 수 :", like_cnt1)

                    # text
                    text1 = post_box.find(name='div', attrs={'id':'userct'}).text.strip().replace("\n","")
                    print('게시물 내용 :', text1) 

                    # com_cnt
                    try :                    
                        com_cnt1 = post_box.find(name='span', attrs={'id':'cmcnt'}).text
                        com_cnt1 = int(com_cnt1)
                    except :
                        com_cnt1 = 0
                                                                                                                                         
                    print("댓글 수 :", com_cnt1)

                    # com_text
                    com_box = post_box.find(name='div', attrs={'class':'comment_inbox'}).find_all('li')
                    com_list = []
                    user_list = []

                    for j in com_box :

                        if len(j) > 1 :  

                            try :
                                # comment_user_id
                                com_user = j.find(name='span', attrs={'class':'cname'}).text

                                com_text = j.find(name='div', attrs={'class':'cmt-contents'}).text.strip().replace("\n","")
                                com_list.append("작성자 :" + com_user + " :: " + com_text)
                                user_list.append(com_user)
                            except :
                                print("삭제된 댓글입니다.")

                    print("게시물 작성자 :", user_list)
                    print('게시물 댓글 :', com_list)
                    
                    domain2.append(domain1)
    #                 keyword2.append(keyword)
                    title2.append(title1)
                    user2.append(user1)
                    url2.append(target_url)
                    time2.append(time1)
                    view_cnt2.append(view_cnt1)
                    like_cnt2.append(like_cnt1)
                    text2.append(text1)
                    com_cnt2.append(com_cnt1)
                    com_user2.append(user_list)
                    com_text2.append(com_list)

                    print("\n")
                    
                except :
                    print('삭제된 게시물입니다.')
                    domain2.append(domain1)
    #                 keyword2.append(keyword)
                    title2.append('삭제된 게시물입니다.')
                    user2.append('삭제된 게시물입니다.')
                    url2.append('삭제된 게시물입니다.')
                    time2.append('삭제된 게시물입니다.')
                    view_cnt2.append(0)
                    like_cnt2.append(0)
                    text2.append('삭제된 게시물입니다.')
                    com_cnt2.append(0)
                    com_user2.append('삭제된 게시물입니다.')
                    com_text2.append('삭제된 게시물입니다.')
            
            elif post_day[:2] != "21":
                pass                

            else :
                print("크롤링을 완료했습니다.")
                print('href :',i.find(name='td', attrs={'class':'sbj'}).find('a')['href'] )
                while_code = 1
                break
        
    page_num -= 1


False True False True
21-05-01 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729971&no=38626751
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729971&no=38626751
domain : SLR CLUB
title : ['현금수송차 총격 실제상황 영상']
user_id : Pentax1
작성 시간 : 2021-05-01 22:37:03
조회수 : 14498
공감/좋아요 수 : 8
게시물 내용 : 와 이런 영상 처음봤는데 저 운전자 진짜 장난 아니네요 ㄷㄷㄷhttp://www.youtube.com/watch?v=M6qEee1_4fw
댓글 수 : 68
게시물 작성자 : ['네셔날지오트래픽', '독불장군™', '오래된자게이', '페이퍼로드', '소라와오이', '방사능폐기물', '폴폴나라', 'Pentax1', 'Port.9', 'Selim™', '열대펭귄', '구쉐프', '짭조름한고래밥', 'Jackpot9', 'celedonio', '스타크', 'SugarB', 'Pentax1', '@무침™', '그래서했어요?안했어요?', '[S5%]은지동은아범', '미친자들의함성', '면도기', '와이키키', '께로피', '▶◀머슬링', '방랑운객', 'Byyul', '딸기와포도', '닉네임바꿨어요', '[30D]바스키아', '[z6]라미드우프닉스', 'nuguges', '홈뿌라스', '샴스핑', 'Pro1', '따라따라딴', '하데스99', 'letranger', 'Lovely2018', '하데스99', 'horrorqing', '▶◀Lv7.벨라모빌', '튜더', 'TONGPOO', 'se-12', '▒▒▒▒▒▒', 'se-12', '하이하바', 'se-12', '내일뜨는해', '닉넴뭐로해', 'alss', '나무소리♥', 'vipsjoh', '네이르미뭐니', '은빛호수', '앵두와사과', '앵두와사과', 'valentii',

domain : SLR CLUB
title : ['컨셉카 디자인 그대로 나온 차']
user_id : 우라칸LP610-4
작성 시간 : 2021-05-01 22:29:06
조회수 : 1600
공감/좋아요 수 : 0
게시물 내용 : 컨셉양산 (손잡이만 달고 나오는듯)토니스타크가 그립습니다.
댓글 수 : 3
게시물 작성자 : ['스타크', '끄라운', '파파넥']
게시물 댓글 : ['작성자 :스타크 :: 저 아세요? ㅡㅡ', '작성자 :끄라운 :: 간지류 사고싶단 ㄷㄷㄷㄷㄷㄷ', '작성자 :파파넥 :: 미등은 현기네']


False True False True
21-05-01 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729971&no=38626737
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729971&no=38626737
domain : SLR CLUB
title : ['너부리들. GIF']
user_id : 52w
작성 시간 : 2021-05-01 22:28:54
조회수 : 1402
공감/좋아요 수 : 0
게시물 내용 : ...정직한 제목
댓글 수 : 3
게시물 작성자 : ['폴폴나라', '짭조름한고래밥', '사악한엘피앙']
게시물 댓글 : ['작성자 :폴폴나라 :: 할퀴면 살작 긁혀도 파상풍주사 꼭꼭...!!!', '작성자 :짭조름한고래밥 :: 심장에 위험한 짤..', '작성자 :사악한엘피앙 :: 광견병 주의...']


False True False True
21-05-01 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729971&no=38626736
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729971&no=38626736
domain : SLR CLUB
title : ['강원도는 눈와서 아이스 타이어 꼈나요?']
user_

domain : SLR CLUB
title : ['남자들 우르르 모였다가 해산하는 짤 있지 않았나요?']
user_id : 「강군」
작성 시간 : 2021-05-01 22:24:40
조회수 : 191
공감/좋아요 수 : 0
게시물 내용 : 예쁜여자보고 막 모였다가 앞모습보고 해산하는 짤 없나여 ㅠㅠ
댓글 수 : 0
게시물 작성자 : []
게시물 댓글 : []


False True False True
21-05-01 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729971&no=38626724
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729971&no=38626724
domain : SLR CLUB
title : ['메구리 당분간 활동 접는다. JPG']
user_id : 52w
작성 시간 : 2021-05-01 22:23:59
조회수 : 1678
공감/좋아요 수 : 0
게시물 내용 : 정직한 제목
댓글 수 : 5
게시물 작성자 : ['독불장군™', 'SugarB', 'Lv7.리얼맨', '그레하', '조정간단발좌유나']
게시물 댓글 : ['작성자 :독불장군™ :: ㄷㄷㄷㄷㄷㄷㄷ', '작성자 :SugarB :: 비말목욕 ㄷㄷㄷ', '작성자 :Lv7.리얼맨 :: 메구리님은 보호해야한다고 생각합니다', '작성자 :그레하 :: 글이 귀여워', '작성자 :조정간단발좌유나 :: ㅠㅠ']


False True False True
21-05-01 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729971&no=38626723
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729971&no=38626723
domain : SLR CLUB
title : ['구k9 운행하시는 자게이님들ㄷㄷ']
user_id : 지금여긴예전자게가아니야
작성 시간 : 2021-0

domain : SLR CLUB
title : ['만화책 보는 사이트 좀...']
user_id : 악마는브라자를입는다
작성 시간 : 2021-05-01 22:17:45
조회수 : 213
공감/좋아요 수 : 0
게시물 내용 : 심심해서 만화책 좀 보려는데, 좋은 사이트 아시나요?
댓글 수 : 2
게시물 작성자 : ['끄라운', 'Lv7.꺼부기']
게시물 댓글 : ['작성자 :끄라운 :: 마루마루?', '작성자 :Lv7.꺼부기 :: 툰코나혼자만 레벨업 안보셧다면 보세요 오늘 밤샙니다']


False True False True
21-05-01 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729970&no=38626710
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729970&no=38626710
domain : SLR CLUB
title : ['며칠전 소개팅을 했는데 여자가 처음하는 질문이']
user_id : 페이퍼로드
작성 시간 : 2021-05-01 22:17:07
조회수 : 830
공감/좋아요 수 : 0
게시물 내용 : 카페에서 처음 얼굴 보고 저는 인사를 했는데 상대방은 인사를 하는둥 마는둥 하면서 자리에 앉더니 처음 하는말이뭐 타고 오셨어요? 직업이 뭐에요? 이런 질문을 하더군요제가 너무 민감한 건가요?
댓글 수 : 30
게시물 작성자 : ['만인적', '오드아이™', '숭고한백수의삶', '공동인증서', 'lIlIIIlIlIIIlI', '티시밀', '바람이온다', '한제희', '이슬:D™', '페이퍼로드', '이슬:D™', '인도르', 'nuII', '끄라운', 'FreddieMucury', '죠스바v', '페이퍼로드', '강퇴더럽군', '몽츠', '푸라비다', '갸가갸가가', '페이퍼로드', '갸가갸가가', '페이퍼로드', '갸가갸가가', '페이퍼로드', '월드박', '오래된자게이', '/으랏차차/', '닥터후_타디스']
게시물 댓글 :

domain : SLR CLUB
title : ['폰을 바꿔도 감흥이 없네요.']
user_id : Wideman
작성 시간 : 2021-05-01 22:11:49
조회수 : 350
공감/좋아요 수 : 0
게시물 내용 : 예전에는 폰 구매하면 신기해서 이것저것 만져보고 그랬는데..요즘은 폰을 구매해도..이전과 똑같은 안드로이드에..바탕화면 아이콘도 이전과 비슷하게 배치해두고..그러다보니 그냥 껍데기만 바뀐 느낌이네요.100만원짜리나...50만원짜리나 감흥이 없네요..ㅠ게임 안하고, 사진 안찍고, 삼페 안쓰고....카톡, 네이버 검색, 통화 문자 끝입니다..새로운걸 써보고 싶은데..아이폰을 한번 사용해보면 어떨까 생각해보네요.
댓글 수 : 25
게시물 작성자 : ['스타크', 'Wideman', '페이퍼로드', 'Wideman', '72365', 'Wideman', '[♩]녹색짐승', 'Wideman', '[♩]녹색짐승', '[♩]녹색짐승', '#사진', 'Wideman', '티시밀', 'Wideman', '티시밀', '토사구팽', 'Wideman', 'MP5¶', 'Wideman', '기상청개객기', 'Wideman', '72365', '아리수.', 'Wideman', '아리수.']
게시물 댓글 : ['작성자 :스타크 :: 아이폰 써도 똑같아요', '작성자 :Wideman :: [스타크]아이폰도 똑같은가보네요..', '작성자 :페이퍼로드 :: 아이폰을 사면 느낌이 다르죠 며치지나면 동일하지만게임이나 사진에 민감하지 않다면 굳이 비싼폰 구입할 필요가 없음', '작성자 :Wideman :: [페이퍼로드]컴퓨터도 윈도우만 사용하다,이번에 맥으로 집, 사무실 컴을 바꿨는데..뭔가 좀 새롭고 신기하더라구요..그래서 아이폰을 바꿔 볼까 했는데..며칠 지나면 비슷하군요..^^', '작성자 :72365 :: 상향평준화... 뭘사도 다 비슷하게좋아여', '작성자 :Wideman :: [72365]네..딱 상향평준화 같아요.비슷비슷해요...플래그쉽 모델 구매해도...이것이 좋다

...

domain : SLR CLUB
title : ['발기금지가 교칙(성진국 감성)']
user_id : 국산티비
작성 시간 : 2021-04-30 02:09:56
조회수 : 6548
공감/좋아요 수 : 0
게시물 내용 : ㄷㄷ
댓글 수 : 4
게시물 작성자 : ['해삼깡*ㅡ_-);', '최종병기', '킹팬더', '맞춘법파개자']
게시물 댓글 : ['작성자 :해삼깡*ㅡ_-); :: 일단 와꾸로만 보자면 저는 못세울것같네욤', '작성자 :최종병기 :: 괜찮아 이미 고자야', '작성자 :킹팬더 :: 노발기 가능 ㅋㅋ', '작성자 :맞춘법파개자 :: 저는 스치기만해도 발기될듯 해서 퇴학당하겠네요']


False True False True
21-04-30 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729885&no=38623472
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729885&no=38623472
domain : SLR CLUB
title : ['즐잠들 하시오. GIF']
user_id : 52w
작성 시간 : 2021-04-30 02:06:41
조회수 : 3632
공감/좋아요 수 : 1
게시물 내용 : ......즈르잠
댓글 수 : 3
게시물 작성자 : ['사슴전병1500원', '♥bluebird™', '^^추운나라']
게시물 댓글 : ['작성자 :사슴전병1500원 :: 맛있겠다', '작성자 :♥bluebird™ :: 위산이 올라와 속이 쓰리네요!병원비 청구 하겠습니다!', '작성자 :^^추운나라 :: .........................................................................................................^^']


False True False True
21-04-30 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=

False True False True
21-04-30 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729883&no=38623429
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729883&no=38623429
domain : SLR CLUB
title : ['대구 바람 엄청 부네요;;']
user_id : 강퇴더럽군
작성 시간 : 2021-04-30 00:58:53
조회수 : 2627
공감/좋아요 수 : 0
게시물 내용 : 달구벌 대로에 온동네 쓰레기 다 날라다님...조심들하셈
댓글 수 : 14
게시물 작성자 : ['sns', '강퇴더럽군', '예라이', '강퇴더럽군', 'cooool~', '강퇴더럽군', 'Red-i™', 'BK핵잠수함', 'cooool~', '강퇴더럽군', '매헌™', '강퇴더럽군', '나토얀하랑', '강퇴더럽군']
게시물 댓글 : ['작성자 :sns :: 김제도 그래유바람소리에 깼녜유', '작성자 :강퇴더럽군 :: [sns]아이고 언능 다시 주무세요~~', '작성자 :예라이 :: 태풍오는가요?.. 웬 바람이 이리 무섭게 불어대는지', '작성자 :강퇴더럽군 :: [예라이]저도 놀라서 태풍오나 찾아봤어요;;', '작성자 :cooool~ :: 수성못 나갔다..  먼지바람 ㄷㄷㄷㄷㄷㄷ from SLRoid', '작성자 :강퇴더럽군 :: [cooool~]송해공원 한바퀴 돌고오려했는데 그냥 있으려구요 ㄷ ㄷ', '작성자 :Red-i™ :: [cooool~]자라 만데 돌아뎅기노', '작성자 :BK핵잠수함 :: [강퇴더럽군]달서구 이신듯 ㅌㅌㅌ', '작성자 :cooool~ :: [Red-i™]못에 앉아 캔맥 마시다 도망왔다는..  from SLRoid', '작성자 :강퇴더럽군 :: [BK핵잠수함]달성군입니당 ㅋㅋㅋ', '작성자 :매헌™ :: 서울은 비 많이 내림. 장마 느낌. ㄷ ㄷ 지금도 계속 내림', '작성자 :강퇴더럽군 :: [매헌™]

domain : SLR CLUB
title : ['금과 비트코인']
user_id : Rs9000x
작성 시간 : 2021-04-30 00:45:43
조회수 : 14141
공감/좋아요 수 : 3
게시물 내용 : 금에 가치도 보이지 않은 가상에 대한 가치도결국은 인간이 부여함. -> 그 인간들이 이제 누구냐를 보세요.현실에 그 가치가 현물이냐? 아니냐?는절대 중요하지 않음.보이지 않는 자산에 가치를 인간이 부여하면그 가치가 1억도 10억도 될 수 있음.일례로 튤립이었겠네요.....알아서들...
댓글 수 : 175
게시물 작성자 : ['Omura', '카드쪼는푸우', 'Rs9000x', 'Omura', 'Rs9000x', '짱921', 'FreeFloat', 'AOA', 'Rolandpark', '도로프', '찬스냅', '구리굴릉', 'alska79', '언제나 네 곁에', '구리굴릉', '키오스크', '자게보고자게', '효성', '♩▶해파리◀', '비오는날에', '결린어깨', '구리굴릉', '냠냠포도', '코어리스', '(=^工^=)냐옹', 'Rs9000x', '코어리스', '코어리스', '(=^工^=)냐옹', '(=^工^=)냐옹', 'Rs9000x', '코어리스', 'Rs9000x', '(=^工^=)냐옹', '코어리스', '(=^工^=)냐옹', '코어리스', '코어리스', 'Rs9000x', '(=^工^=)냐옹', 'FreeFloat', 'Rs9000x', '라라라지지지', '구리굴릉', '구리굴릉', '키오스크', 'ㅊㅈㅇㅇㅊㄱㄱ', '내친구영희', '키오스크', '♩▶해파리◀', '짱모', '트위치', '㈜자르게이스', '키오스크', '레머스', '카메라는캐논', '한선협국', '넌갈등이었어', '키오스크', '유기농청년', '어게인1981', 'Rs9000x', 'BladeRunner', 'Rs9000x', 'BladeRunner', 'BladeRunner', 'Rs9000x', 'Rs9000x', 'BladeRunner', 'Rs9000x', 'Blad

domain : SLR CLUB
title : ['내가 다녔던 고등학교의 이사장님...  연대 경제학과 나왔는데 세무 공무원 출신']
user_id : 치킨과피자
작성 시간 : 2021-04-30 00:43:26
조회수 : 283
공감/좋아요 수 : 1
게시물 내용 : 땅 사놓은게 천정부지로 올라버려서 40대 나이에 명문 사립중고등학교를 설립하고 이사장으로 취임1930년대 생인데 아직 생존해 계심암튼 예전엔 중학교만 나오고 고등학교만 나온 자들이 공뭔 된줄 아는 사람들 많던데결코 아님...뭐 그런 식이라면 모든 업종이 다 예전보다는 되기가 어려워진거 같은데유독 공무원만 예전엔 떨거지들이 됐던걸로 알더라구요.
댓글 수 : 0
게시물 작성자 : []
게시물 댓글 : []


False True False True
21-04-30 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729883&no=38623418
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729883&no=38623418
domain : SLR CLUB
title : ['역시 도지는 대마불사']
user_id : 소나무/테스형
작성 시간 : 2021-04-30 00:41:18
조회수 : 409
공감/좋아요 수 : 1
게시물 내용 : 제말듣고 매수하신분이 위너임
댓글 수 : 1
게시물 작성자 : ['최종병기']
게시물 댓글 : ['작성자 :최종병기 :: 일론 머스크는 도지 사긴 샀을까?']


False True False True
21-04-30 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729883&no=38623417
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729883&no=38623417
domain : SLR CLUB
title : ['이 ufo는 진짜 개멋있네요']
u

domain : SLR CLUB
title : ['K1 최홍만 vs 바다하리']
user_id : 봄날의커피
작성 시간 : 2021-04-30 00:25:54
조회수 : 381
공감/좋아요 수 : 0
게시물 내용 : http://youtu.be/VgEP304GtoA크체격이 정말 갑이군요느린 스피드는 어쩔 수 없나 봄
댓글 수 : 0
게시물 작성자 : []
게시물 댓글 : []


False True False True
21-04-30 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729883&no=38623405
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729883&no=38623405
domain : SLR CLUB
title : ['코인? 나쁘다곤 생각 안합니다.']
user_id : mj1234
작성 시간 : 2021-04-30 00:25:18
조회수 : 264
공감/좋아요 수 : 0
게시물 내용 : 결국 미국에서 디지털달러 선언해버리면 끝이니까요그거 모르고 투자하는 사람 없습니다수익이 날수만 있다면 좋은 자산이죠.
댓글 수 : 0
게시물 작성자 : []
게시물 댓글 : []


False True False True
21-04-30 21-05-01 21-04-30
href : /bbs/vx2.php?id=free&page=729883&no=38623402
target_url : http://www.slrclub.com/bbs/vx2.php?id=free&page=729883&no=38623402
domain : SLR CLUB
title : ['야밤 홈카페 야밤 커피']
user_id : 토닥이™
작성 시간 : 2021-04-30 00:18:53
조회수 : 868
공감/좋아요 수 : 0
게시물 내용 : ......밤엔 커피죠!원두 테스트 중인데, 이건 생각보다 그냥 그러네요
댓글 수 : 10
게시물 작성자 : ['은돌민돌아빠', '토닥이™',

In [12]:
df = pd.DataFrame()

df['domain'] = pd.Series(domain2)
# df['keyword'] = pd.Series(keyword2)
df['title'] = pd.Series(title2)
df['user_name'] = pd.Series(user2)
df['url'] = pd.Series(url2)
df['date'] = pd.Series(time2)
df['view_cnt'] = pd.Series(view_cnt2)
df['like_cnt'] = pd.Series(like_cnt2)
df['user_text'] = pd.Series(text2)
df['com_cnt'] = pd.Series(com_cnt2)
df['com_text'] = pd.Series(com_text2)

df

domain                                         title     writer  \
0     SLR CLUB                            [현금수송차 총격 실제상황 영상]    Pentax1   
1     SLR CLUB                    [요즘 길가다가 번호 물어보면 ㅊㅈ한테 뺨맞음]       ＬＯＶＥ   
2     SLR CLUB                                  [미나리 일본버전…?]        링링♩   
3     SLR CLUB  [아이의 성을 아빠성으로 쓸 경우에 대한 댓가까지 분명하게 짚고 들어가셔야죠.]      치킨과피자   
4     SLR CLUB                      [52w형이 퍼오는글의 선정기준이 뭔가요?]       레드박스   
...        ...                                           ...        ...   
2291  SLR CLUB                               [상장을 앞둔 와이프 회사]  Singapore   
2292  SLR CLUB                      [페미들은 결혼은 무엇 하러 한 것일까요?]      철장수상표   
2293  SLR CLUB            [서산에서 대중교통 타고 청주 공항 가서 제주도 다녀온 후기]      콘실리에레   
2294  SLR CLUB                                   [SoSo ㄷㄷㄷㄷ]      오다길이죠   
2295  SLR CLUB                                   [현직 모텔 입니다]     doutor   

                                                    url                 time  \
0     http://www.slrclub.com/bbs/vx2.php?id=free&pag...  2021-05-01 22:37:03   
1     http://www.slrclub.com/bbs/vx2.php?id=free&pag...  2021-05-01 22:35:19   
2     http://www.slrclub.com/bbs/vx2.php?id=free&pag...  2021-05-01 22:34:15   
3     http://www.slrclub.com/bbs/vx2.php?id=free&pag...  2021-05-01 22:34:10   
4     http://www.slrclub.com/bbs/vx2.php?id=free&pag...  2021-05-01 22:33:32   
...                                                 ...                  ...   
2291  http://www.slrclub.com/bbs/vx2.php?id=free&pag...  2021-04-30 00:08:21   
2292  http://www.slrclub.com/bbs/vx2.php?id=free&pag...  2021-04-30 00:07:02   
2293  http://www.slrclub.com/bbs/vx2.php?id=free&pag...  2021-04-30 00:05:28   
2294  http://www.slrclub.com/bbs/vx2.php?id=free&pag...  2021-04-30 00:03:14   
2295  http://www.slrclub.com/bbs/vx2.php?id=free&pag...  2021-04-30 00:01:04   

     view_cnt like_cnt                                            content  \
0       14498        8  와 이런 영상 처음봤는데 저 운전자 진짜 장난 아니네요 ㄷㄷㄷhttp://www.y...   
1         493        0                                  코로나 시국에 말건다고 뺨맞았음   
2        1263        0  왓챠에서 우연히 봤는데..약간 미나리 일본 버전 느낌이네요.1960년대 후반 일본 ...   
3         220        1  「출산에 대한 댓가와 육아방식, 아이의 성을 아빠성으로 쓸 경우에 대한 댓가까지 분...   
4         160        0  매번 글을 보다보니 궁금해졌어요예전엔 이슈나 선정성 위주였는데요즘엔 문화나 다큐 위...   
...       ...      ...                                                ...   
2291     1056        0         우리사주로 과연 얼마나 벌 것인지..G80 사고 싶다고 말햐뒀는대 과연 ㅋㅋ   
2292      281        0  페미들 한테는 남성은 무조건 적 아닌가요?그런 남성과결혼하고 자식 낳고 사는 여자들...   
2293      273        1                       오지게 힘드네요서산도 공항 좀 생겼으면 좋겠습니다.   
2294     1204        0              사장의 인성을 터트린 쏘쏘 ㄷㄷㄷ저런 새끼들이 자영업을 하네 ㄷㄷㄷ   
2295    12671        1  코로나 소독 했다고 해서 왔는데담배냄새 쩔어서 환기중임다하긴 2만2천원에 뭘기대를 ...   

      com_cnt                                           com_text  
0          68  [작성자 :네셔날지오트래픽 :: 1분 9초부터, 작성자 :독불장군™ :: ㄷㄷㄷㄷㄷ...  
1           3  [작성자 :쭈꾸루 :: 과연!!, 작성자 :K.S.H :: 케이스바이케이스, 작성자...  
2           5  [작성자 :스테이플러 :: 와사비?, 작성자 :티이™ :: [스테이플러]악 ㅋㅋㅋㅋ...  
3           2  [작성자 :철장수상표 :: 뉴규??, 작성자 :치킨과피자 :: [철장수상표]판녀 ㄷㄷㄷ]  
4           0                                                 []  
...       ...                                                ...  
2291        5  [작성자 :CHALONER :: 치킨 줄섭니다, 작성자 :mj1234 :: 상장이 ...  
2292        7  [작성자 :윤지삼츈™ :: 애인 생기기전 까지만  페미그래야 있어보이니까 ㅎㅎ, 작...  
2293        0                                                 []  
2294        4  [작성자 :Lv7.Κοοki™ :: 16시간을 일해서 맛이 쏘쏘하면 그냥 접어도 될...  
2295       44  [작성자 :끄라운 :: 구미에 뭐가 없어유..... 밤에 다니면 유흥가 말곤 그냥 ...  

[2296 rows x 10 columns]

In [13]:
# csv 형태로 저장하기
df.to_csv(fc_name,encoding="utf-8-sig",index=False)

e_time = time.time( )
t_time = e_time - s_time

print("\n")
print("=" *80)
print("1.총 소요시간은 %s 초 입니다 " %round(t_time,1))
print("2.파일 저장 완료: csv 파일명 : %s " %fc_name)

driver.quit()
sys.exit("프로그램을 종료합니다.")



1.총 소요시간은 4840.4 초 입니다 
2.파일 저장 완료: csv 파일명 : C:\Users\JPARK-02\Desktop\crawler-bot\COMMUNITY\2021-04-30-2021-05-01\\slr3.csv 


SystemExit: 프로그램을 종료합니다.

c:\python39\lib\site-packages\IPython\core\interactiveshell.py:3449: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
